In [1]:
### 形態素解析
import MeCab

#text = "私はお昼休みに美味しいカレーライスを食べました。"

m = MeCab.Tagger("-Ochasen")

def mecab_sep(text):
    node = m.parseToNode(text)

    words_list = []

    while node:
        if node.feature.split(",")[0] == "動詞":
            words_list.append(node.feature.split(",")[6])
        elif node.feature.split(",")[0] == "形容詞":
            words_list.append(node.feature.split(",")[6])
        else:
            words_list.append(node.surface)

        node = node.next
        
    return words_list[1:-1]

In [6]:
### Bag-of-words / tf-idf
from sklearn.feature_extraction.text import TfidfVectorizer

def calc_vecs(docs):
    vectorizer = TfidfVectorizer(analyzer=mecab_sep)
    vecs = vectorizer.fit_transform(docs)
    return vecs.toarray()


In [15]:
### コサイン類似度
import numpy as np
import pandas as pd
from sklearn.metrics.pairwise import cosine_similarity

input_doc = "君はネコが好きです。"

target_docs_df = pd.read_csv("target_docs.csv")
target_docs = target_docs_df["文章リスト"].tolist()

all_docs = [input_doc] + target_docs
all_docs_vecs = calc_vecs_d2v(all_docs)

similarity =cosine_similarity([all_docs_vecs[0]],all_docs_vecs[1:])

target_docs_df["類似度"] = similarity[0]

In [14]:
target_docs_df.sort_values("類似度",ascending=False)

文章リスト       類似度
0      私は犬が好きです。  0.438497
4    あなたは猫が好きです。  0.388658
2   私は犬がとても好きです。  0.354345
3  あなたは犬と猫が好きです。  0.310741
1      私は犬が嫌いです。  0.278822

In [16]:
target_docs_df.sort_values("類似度",ascending=False)

文章リスト       類似度
4    あなたは猫が好きです。  0.924543
3  あなたは犬と猫が好きです。  0.919218
0      私は犬が好きです。  0.907596
1      私は犬が嫌いです。  0.903666
2   私は犬がとても好きです。  0.902655

In [7]:
import glob
target_docs=[]

for x in glob.glob("text/*/*.txt"):
    text = ""
    with open(x) as f:
        next(f)
        next(f)
        for line in f:
            text = text + line
    f.close()
    target_docs.append(text)
